In [1]:
import os
import cv2

# Define gesture labels
gestures = ['Hello', 'Yes', 'No', 'Thank you', 'Sorry', 'Eat', 'Like', 'Want', 'I Love You', 'Which', 'Peace', 'Bathroom']
directory = 'Image/'

# Create directories if they do not exist
for gesture in gestures:
    os.makedirs(os.path.join(directory, gesture), exist_ok=True)

cap = cv2.VideoCapture(0)

while True:
    _, frame = cap.read()

    # Count images in each gesture directory
    count = {gesture: len(os.listdir(os.path.join(directory, gesture))) for gesture in gestures}

    row = frame.shape[1]
    col = frame.shape[0]
    cv2.rectangle(frame, (0, 40), (300, 400), (255, 255, 255), 2)
    cv2.imshow("data", frame)
    cv2.imshow("ROI", frame[40:400, 0:300])
    frame_roi = frame[40:400, 0:300]
    
    interrupt = cv2.waitKey(10)

    if interrupt & 0xFF == ord('q'):
        break

    # Map specific keys to gestures
    key_to_gesture = {
        '1': 'Hello',
        '2': 'Yes',
        '3': 'No',
        '4': 'Thank you',
        '5': 'Sorry',
        '6': 'Eat',
        '7': 'Like',
        '8': 'Want',
        '9': 'I Love You',
        '0': 'Which',
        '-': 'Peace',
        '=': 'Bathroom'
    }

    for key, gesture in key_to_gesture.items():
        if interrupt & 0xFF == ord(key):
            cv2.imwrite(os.path.join(directory, gesture, f'{count[gesture]}.png'), frame_roi)
            print(f"Saved image for gesture '{gesture}'")

cap.release()
cv2.destroyAllWindows()

Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved image for gesture 'Hello'
Saved im

In [5]:
from function import *
from time import sleep

# Define gestures
gestures = ['Hello', 'Yes', 'No', 'Thank you', 'Sorry', 'Eat', 'Like', 'Want', 'I Love You', 'Which', 'Peace', 'Bathroom']

for gesture in gestures: 
    for sequence in range(no_sequences):
        try: 
            os.makedirs(os.path.join(DATA_PATH, gesture, str(sequence)))
        except:
            pass

# Set mediapipe model 
with mp_hands.Hands(
    model_complexity=0,
    min_detection_confidence=0.5,
    min_tracking_confidence=0.5) as hands:
    
    # NEW LOOP
    # Loop through gestures
    for gesture in gestures:
        # Loop through sequences
        for sequence in range(no_sequences):
            # Loop through sequence length (frames)
            for frame_num in range(sequence_length):

                # Read image
                frame = cv2.imread('Image/{}/{}.png'.format(gesture, sequence))

                # Make detections
                image, results = mediapipe_detection(frame, hands)

                # Draw landmarks
                draw_styled_landmarks(image, results)
                
                # NEW Apply wait logic
                if frame_num == 0:
                    cv2.putText(image, 'STARTING COLLECTION', (120,200), 
                               cv2.FONT_HERSHEY_SIMPLEX, 1, (0,255, 0), 4, cv2.LINE_AA)
                    cv2.putText(image, 'Collecting frames for {} Sequence {}'.format(gesture, sequence), (15,12), 
                               cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                    # Show to screen
                    cv2.imshow('OpenCV Feed', image)
                    cv2.waitKey(200)
                else: 
                    cv2.putText(image, 'Collecting frames for {} Sequence {}'.format(gesture, sequence), (15,12), 
                               cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                    # Show to screen
                    cv2.imshow('OpenCV Feed', image)
                
                # NEW Export keypoints
                keypoints = extract_keypoints(results)
                npy_path = os.path.join(DATA_PATH, gesture, str(sequence), str(frame_num))
                np.save(npy_path, keypoints)

                # Break gracefully
                if cv2.waitKey(10) & 0xFF == ord('q'):
                    break
                    
    cv2.destroyAllWindows()

C:\Users\yaski\anaconda3\Lib\site-packages\google\protobuf\symbol_database.py:55: UserWarning: SymbolDatabase.GetPrototype() is deprecated. Please use message_factory.GetMessageClass() instead. SymbolDatabase.GetPrototype() will be removed soon.
  warnings.warn('SymbolDatabase.GetPrototype() is deprecated. Please '


In [11]:
from sklearn.model_selection import train_test_split
from keras.utils import to_categorical 
from keras.models import Sequential
from keras.layers import LSTM, Dense 
from keras.callbacks import TensorBoard 
import os
import numpy as np

# Path for exported data, numpy arrays
DATA_PATH = os.path.join('MP_Data')

# Define gestures
gestures = ['Hello', 'Yes', 'No', 'Thank you', 'Sorry', 'Eat', 'Like', 'Want', 'I Love You', 'Which', 'Peace', 'Bathroom', 'Good', 'Bad', 'Stop', 'Money', 'Happy', 'Phone', 'Hear', 'See', 'Drink', 'Walk']

no_sequences = 30  # Number of sequences per gesture
sequence_length = 30  # Length of each sequence

label_map = {label: num for num, label in enumerate(gestures)}
sequences, labels = [], []

for gesture in gestures:
    for sequence in range(no_sequences):
        window = []
        for frame_num in range(sequence_length):
            try:
                res = np.load(os.path.join(DATA_PATH, gesture, str(sequence), "{}.npy".format(frame_num)))
                window.append(res)
            except FileNotFoundError:
                print(f"File not found: {os.path.join(DATA_PATH, gesture, str(sequence), '{}.npy'.format(frame_num))}")
        sequences.append(window)
        labels.append(label_map[gesture])

X = np.array(sequences)
y = to_categorical(labels).astype(int)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.05)

log_dir = os.path.join('Logs')
tb_callback = TensorBoard(log_dir=log_dir)

model = Sequential()
model.add(LSTM(64, return_sequences=True, activation='relu', input_shape=(sequence_length, 63)))
model.add(LSTM(128, return_sequences=True, activation='relu'))
model.add(LSTM(64, return_sequences=False, activation='relu'))
model.add(Dense(64, activation='relu'))
model.add(Dense(32, activation='relu'))
model.add(Dense(len(gestures), activation='softmax'))  # Adjust output shape to match the number of gestures

model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['categorical_accuracy'])
model.fit(X_train, y_train, epochs=81, callbacks=[tb_callback])
model.summary()

# Save model architecture as JSON
model_json = model.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)

model.save('model.keras')


C:\Users\hrith\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 4s 43ms/step - categorical_accuracy: 0.0821 - loss: 3.0696
Epoch 2/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 49ms/step - categorical_accuracy: 0.1222 - loss: 2.6559
Epoch 3/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 48ms/step - categorical_accuracy: 0.2291 - loss: 2.4721
Epoch 4/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 43ms/step - categorical_accuracy: 0.4123 - loss: 1.8562
Epoch 5/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 45ms/step - categorical_accuracy: 0.4503 - loss: 1.7432
Epoch 6/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 47ms/step - categorical_accuracy: 0.6051 - loss: 1.3309
Epoch 7/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 44ms/step - categorical_accuracy: 0.4855 - loss: 1.5352
Epoch 8/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 44ms/step - categorical_accuracy: 0.6309 - loss: 1.0855
Epoch 9/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 48ms/step - categorical_accuracy: 0.7209 - loss: 0.8665
Epoch 10/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 44ms/step - categorical_accuracy: 0.8188 - loss: 0.5510
Epoch 11/81
20/20 ━━━━━━━━━━━

20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - categorical_accuracy: 1.0000 - loss: 2.4978e-04
Epoch 63/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - categorical_accuracy: 1.0000 - loss: 2.0175e-04
Epoch 64/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 44ms/step - categorical_accuracy: 1.0000 - loss: 1.7614e-04
Epoch 65/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - categorical_accuracy: 1.0000 - loss: 1.4852e-04
Epoch 66/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 41ms/step - categorical_accuracy: 1.0000 - loss: 1.6838e-04
Epoch 67/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 40ms/step - categorical_accuracy: 1.0000 - loss: 1.7760e-04
Epoch 68/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - categorical_accuracy: 1.0000 - loss: 1.5232e-04
Epoch 69/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 40ms/step - categorical_accuracy: 1.0000 - loss: 1.9733e-04
Epoch 70/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step - categorical_accuracy: 1.0000 - loss: 1.2429e-04
Epoch 71/81
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - categorical_accuracy: 1.0000 - loss: 1.0

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ lstm (LSTM)                          │ (None, 30, 64)              │          32,768 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm_1 (LSTM)                        │ (None, 30, 128)             │          98,816 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm_2 (LSTM)                        │ (None, 64)                  │          49,408 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 64)                  │           4,160 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_1 (Dense)                      │ (None, 32)                  │           2,080 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_2 (Dense)                      │ (None, 22)                  │             726 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 563,876 (2.15 MB)

 Trainable params: 187,958 (734.21 KB)

 Non-trainable params: 0 (0.00 B)

 Optimizer params: 375,918 (1.43 MB)

In [12]:
import cv2
import numpy as np
import mediapipe as mp
from keras.models import model_from_json
from function import mediapipe_detection, extract_keypoints

gestures = ['Hello', 'Yes', 'No', 'Thank you', 'Sorry', 'Eat', 'Like', 'Want', 'I Love You', 'Which', 'Peace', 'Bathroom', 'Good', 'Bad', 'Stop', 'Money', 'Happy', 'Phone', 'Hear', 'See', 'Drink', 'Walk']

# Load the model
json_file = open("model.json", "r")
model_json = json_file.read()
json_file.close()
model = model_from_json(model_json)
model.load_weights("model.keras")

# Define colors for probability visualization
colors = [(245, 117, 16) for _ in range(len(gestures))]

def prob_viz(res, gestures, input_frame, colors, threshold):
    output_frame = input_frame.copy()
    for num, prob in enumerate(res):
        cv2.rectangle(output_frame, (0, 60 + num * 40), (int(prob * 100), 90 + num * 40), colors[num], -1)
        cv2.putText(output_frame, gestures[num], (0, 85 + num * 40), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2,
                    cv2.LINE_AA)
    return output_frame

def draw_hand_bbox(image, results, margin=20):
    bbox_coords = None
    if results.multi_hand_landmarks:
        for hand_landmarks in results.multi_hand_landmarks:
            h, w, c = image.shape
            x_min = w
            y_min = h
            x_max = y_max = 0
            for landmark in hand_landmarks.landmark:
                x, y = int(landmark.x * w), int(landmark.y * h)
                if x < x_min:
                    x_min = x
                if y < y_min:
                    y_min = y
                if x > x_max:
                    x_max = x
                if y > y_max:
                    y_max = y
            # Add margin to the bounding box
            x_min = max(0, x_min - margin)
            y_min = max(0, y_min - margin)
            x_max = min(w, x_max + margin)
            y_max = min(h, y_max + margin)
            bbox_coords = (x_min, y_min, x_max, y_max)
            cv2.rectangle(image, (x_min, y_min), (x_max, y_max), (0, 255, 0), 2)
    return image, bbox_coords

# New detection variables
sequence = []
sentence = []
predictions = []
threshold = 0.8

cap = cv2.VideoCapture(0)
# cap = cv2.VideoCapture("https://192.168.43.41:8080/video")

# Create a named window
cv2.namedWindow('OpenCV Feed', cv2.WND_PROP_FULLSCREEN)
cv2.setWindowProperty('OpenCV Feed', cv2.WND_PROP_FULLSCREEN, cv2.WINDOW_FULLSCREEN)

# Set mediapipe model
mp_hands = mp.solutions.hands

try:
    with mp_hands.Hands(
            model_complexity=0,
            min_detection_confidence=0.5,
            min_tracking_confidence=0.5) as hands:
        while cap.isOpened():

            # Read feed
            ret, frame = cap.read()
            if not ret:
                break

            # Make detections
            cropframe = frame[40:400, 0:300]

            image, results = mediapipe_detection(cropframe, hands)
            image, bbox_coords = draw_hand_bbox(image, results, margin=40)  # Increased margin

            if results.multi_hand_landmarks:
                keypoints = extract_keypoints(results)
                if keypoints is not None:
                    print(f"Keypoints: {keypoints}")  # Debugging line to print keypoints
                    sequence.append(keypoints)
                    sequence = sequence[-30:]

                    if len(sequence) == 30:
                        try:
                            res = model.predict(np.expand_dims(sequence, axis=0))[0]
                            print(f"Prediction: {res}")  # Debugging line to print prediction results
                            predictions.append(np.argmax(res))

                            if np.unique(predictions[-10:])[0] == np.argmax(res):
                                if res[np.argmax(res)] > threshold:
                                    if len(sentence) > 0:
                                        if gestures[np.argmax(res)] != sentence[-1]:
                                            sentence.append(gestures[np.argmax(res)])
                                    else:
                                        sentence.append(gestures[np.argmax(res)])

                            if len(sentence) > 1:
                                sentence = sentence[-1:]
                        except Exception as e:
                            print(e)
                            pass

            else:
                sequence = []  # Reset the sequence if no hand is detected
                sentence = []

            # Overlay the processed image back onto the frame
            frame[40:400, 0:300] = image

            if bbox_coords and sentence:  # Only display output if there's a detected action and bbox
                x_min, y_min, x_max, y_max = bbox_coords
                cv2.rectangle(frame, (x_min, y_min - 40), (x_max, y_min), (245, 117, 16), -1)
                cv2.putText(frame, "Output: " + ' '.join(sentence), (x_min + 3, y_min - 10),
                            cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2, cv2.LINE_AA)

            # Show to screen
            cv2.imshow('OpenCV Feed', frame)

            # Break gracefully
            if cv2.waitKey(10) & 0xFF == ord('q'):
                break
except KeyboardInterrupt:
    pass
finally:
    cap.release()
    cv2.destroyAllWindows()


C:\Users\hrith\AppData\Roaming\Python\Python311\site-packages\google\protobuf\symbol_database.py:55: UserWarning: SymbolDatabase.GetPrototype() is deprecated. Please use message_factory.GetMessageClass() instead. SymbolDatabase.GetPrototype() will be removed soon.
  warnings.warn('SymbolDatabase.GetPrototype() is deprecated. Please '


Keypoints: [ 5.10329366e-01  9.63274360e-01  1.43923300e-08  6.17074072e-01
  9.28238869e-01 -5.80743924e-02  7.13269532e-01  8.39684486e-01
 -1.09135948e-01  7.64744639e-01  7.64695644e-01 -1.61455289e-01
  7.99280405e-01  6.98140442e-01 -2.18142077e-01  6.33373916e-01
  6.80432975e-01 -8.59677270e-02  6.71870708e-01  5.69449723e-01
 -1.53559566e-01  7.01128960e-01  4.96090174e-01 -2.09269509e-01
  7.29851544e-01  4.31651413e-01 -2.53063351e-01  5.49290776e-01
  6.82335258e-01 -1.07492924e-01  5.42847991e-01  5.55945098e-01
 -1.85612068e-01  5.45058310e-01  4.69198912e-01 -2.46825144e-01
  5.49229801e-01  3.93462688e-01 -2.93125242e-01  4.66259837e-01
  7.12463260e-01 -1.34386197e-01  4.62099046e-01  6.31661892e-01
 -2.11295798e-01  4.68511939e-01  5.97852647e-01 -2.52008051e-01
  4.75516498e-01  5.73028564e-01 -2.76680529e-01  3.88319910e-01
  7.58460701e-01 -1.69034943e-01  3.92371058e-01  7.17822969e-01
 -2.30151460e-01  4.22349513e-01  7.19213545e-01 -2.55223334e-01
  4.49110568e-

Keypoints: [ 6.27077341e-01  9.46369290e-01  2.03492245e-08  7.58280754e-01
  8.87241721e-01 -3.41871455e-02  8.60826671e-01  7.98234105e-01
 -5.29581718e-02  9.22196269e-01  7.15038836e-01 -7.71736205e-02
  9.66124177e-01  6.62739813e-01 -1.02467604e-01  7.75271952e-01
  6.56003594e-01  1.97257474e-03  8.27471673e-01  5.41366935e-01
 -1.91804413e-02  8.53372574e-01  4.71040845e-01 -3.90066244e-02
  8.75255704e-01  4.08152491e-01 -5.61853014e-02  6.93837941e-01
  6.38461530e-01 -1.35431616e-02  7.13359475e-01  5.09581149e-01
 -2.66006086e-02  7.24975646e-01  4.31441158e-01 -5.20718545e-02
  7.36068606e-01  3.63125980e-01 -7.57011399e-02  6.13996446e-01
  6.48315847e-01 -3.75364386e-02  5.98374963e-01  5.33048153e-01
 -5.86008653e-02  5.87257504e-01  4.59396958e-01 -8.86103660e-02
  5.83921134e-01  3.95971060e-01 -1.11648463e-01  5.34455895e-01
  6.79899454e-01 -6.81532994e-02  4.86637235e-01  5.92903852e-01
 -8.82317573e-02  4.61991847e-01  5.39134920e-01 -1.07038632e-01
  4.45962071e-

Keypoints: [ 5.99184334e-01  9.39962506e-01  2.24058567e-08  7.25021601e-01
  8.79450202e-01 -3.69124897e-02  8.25220048e-01  7.89206684e-01
 -6.21320829e-02  8.90802503e-01  7.07806647e-01 -9.17643160e-02
  9.43018913e-01  6.52612090e-01 -1.23314247e-01  7.31199682e-01
  6.52725458e-01 -2.10419260e-02  7.82858074e-01  5.35540760e-01
 -4.91048433e-02  8.07384729e-01  4.65509772e-01 -7.15753138e-02
  8.27673614e-01  4.01694536e-01 -9.07590985e-02  6.47055507e-01
  6.37622058e-01 -3.73213068e-02  6.56262338e-01  5.08226514e-01
 -5.77291511e-02  6.60046399e-01  4.32116091e-01 -8.39532912e-02
  6.64257407e-01  3.63468349e-01 -1.08672291e-01  5.67205667e-01
  6.51369154e-01 -6.09588698e-02  5.41508019e-01  5.37495136e-01
 -8.89998153e-02  5.22915125e-01  4.65570569e-01 -1.20845065e-01
  5.12692928e-01  4.01223570e-01 -1.45259574e-01  4.91087139e-01
  6.87848032e-01 -9.04156044e-02  4.33316112e-01  6.06365561e-01
 -1.16033137e-01  3.96683872e-01  5.56924582e-01 -1.36591345e-01
  3.68984520e-

Keypoints: [ 5.79481304e-01  9.59075749e-01  2.20952341e-08  7.02416897e-01
  8.92766476e-01 -3.42674032e-02  7.97259808e-01  7.98776150e-01
 -5.99238388e-02  8.59397292e-01  7.16701210e-01 -9.08050984e-02
  9.10045385e-01  6.59587622e-01 -1.23522103e-01  6.98704481e-01
  6.62777841e-01 -1.79455839e-02  7.46872127e-01  5.46643913e-01
 -4.61893827e-02  7.68661380e-01  4.77426469e-01 -6.94411173e-02
  7.86075711e-01  4.13676858e-01 -8.96137282e-02  6.13721192e-01
  6.50791049e-01 -3.67546417e-02  6.13056779e-01  5.22678971e-01
 -5.79450354e-02  6.09789073e-01  4.46971983e-01 -8.58519748e-02
  6.06548667e-01  3.77785712e-01 -1.12256438e-01  5.34595966e-01
  6.69266105e-01 -6.30483180e-02  5.00382125e-01  5.58133066e-01
 -9.31611806e-02  4.76061523e-01  4.87712771e-01 -1.27954006e-01
  4.59151596e-01  4.22609180e-01 -1.54466465e-01  4.60334837e-01
  7.11123943e-01 -9.46583971e-02  3.92088771e-01  6.33514583e-01
 -1.21965460e-01  3.48147660e-01  5.87025046e-01 -1.44233793e-01
  3.13218206e-

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
Prediction: [1.3950971e-10 9.9724907e-01 2.4673287e-05 2.0012950e-21 1.2493821e-13
 1.8956533e-16 3.3402475e-07 3.9704964e-10 5.5280979e-12 1.1378554e-13
 2.9226951e-04 5.1893849e-12 6.1893117e-19 3.4296519e-13 4.7368539e-16
 1.2687765e-07 9.5475235e-16 1.7744173e-20 4.3202659e-16 3.3330047e-11
 5.8702472e-08 2.4334795e-03]
Keypoints: [ 9.06475782e-02  2.44315431e-01  2.61108291e-08  2.50980437e-01
  2.94887185e-01 -9.74719296e-04  3.45575452e-01  4.15435314e-01
 -8.55493173e-02  3.31316710e-01  5.51613629e-01 -1.66178256e-01
  3.02618057e-01  6.41713262e-01 -2.39863411e-01  3.87678623e-01
  4.07546401e-01 -2.63413399e-01  4.80424166e-01  5.70584893e-01
 -3.46090466e-01  5.26660800e-01  6.79730296e-01 -3.80053520e-01
  5.53792655e-01  7.76540995e-01 -4.04617727e-01  2.57478923e-01
  4.09468859e-01 -2.96876967e-01  2.48387158e-01  6.37975693e-01
 -3.80596161e-01  2.42471457e-01  7.67073631e-01 -3.78943712e-01
  2.32081681e-01  8.60251486e-01 -3.8282

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step
Prediction: [2.7878200e-10 9.9323314e-01 2.8067278e-05 3.1285732e-20 6.3033487e-13
 9.5011347e-16 5.0543457e-07 4.7397215e-09 1.7150864e-11 2.6385970e-12
 1.6874134e-03 2.6645072e-11 4.6230314e-18 5.4525449e-13 2.1520045e-15
 6.2201605e-07 3.6218875e-15 2.2690841e-19 5.4945397e-15 3.7973077e-10
 1.5201298e-06 5.0487248e-03]
Keypoints: [ 1.22120366e-01  2.24422038e-01  2.46787071e-08  2.66075820e-01
  2.95953006e-01  4.60091792e-03  3.39873493e-01  4.23829913e-01
 -7.40101188e-02  3.14065635e-01  5.57355821e-01 -1.49803400e-01
  2.77576864e-01  6.48155570e-01 -2.18763888e-01  3.89844835e-01
  4.15404826e-01 -2.48018146e-01  4.52692628e-01  5.82601130e-01
 -3.25087696e-01  4.85668451e-01  6.88335001e-01 -3.53071630e-01
  5.04122972e-01  7.81850934e-01 -3.73303682e-01  2.62819380e-01
  4.08133745e-01 -2.83839494e-01  2.28637636e-01  6.35387480e-01
 -3.61083269e-01  2.13233799e-01  7.63613224e-01 -3.53105754e-01
  1.94611132e-01  8.59318078e-01 -3.5323

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step
Prediction: [8.6102747e-10 9.5967460e-01 9.8566168e-05 4.6882917e-19 7.2481101e-12
 3.6021673e-15 5.3103128e-07 1.6703893e-07 1.3240298e-10 6.2136718e-10
 2.5709445e-02 3.3652674e-09 5.9909350e-17 2.3052458e-12 9.8549615e-15
 5.9889912e-06 5.0881930e-14 1.3360651e-17 3.0079823e-13 3.9536765e-09
 1.9262869e-04 1.4317995e-02]
Keypoints: [ 1.23647608e-01  2.57925034e-01  2.17630483e-08  2.71689415e-01
  3.22382033e-01 -2.36179586e-03  3.51420879e-01  4.47383344e-01
 -8.81240070e-02  3.22628975e-01  5.76024234e-01 -1.67265654e-01
  2.75245577e-01  6.68634892e-01 -2.38557994e-01  3.91376436e-01
  4.32872474e-01 -2.81166732e-01  4.72073436e-01  5.82730711e-01
 -3.70837778e-01  5.14349699e-01  6.83959842e-01 -4.06174898e-01
  5.37482262e-01  7.70536065e-01 -4.28898036e-01  2.59105116e-01
  4.32159603e-01 -3.09290469e-01  2.47740149e-01  6.62867308e-01
 -4.05702502e-01  2.38806069e-01  8.05171669e-01 -4.08515304e-01
  2.19524235e-01  9.05497074e-01 -4.1208

Keypoints: [9.29050922e-01 9.19396758e-01 4.95226260e-09 8.96649539e-01
 8.50618005e-01 8.37534890e-02 8.33217084e-01 8.06145310e-01
 1.29363567e-01 7.89362490e-01 7.58790791e-01 1.59109771e-01
 7.76877224e-01 7.19333053e-01 1.89540088e-01 7.03938484e-01
 8.43157291e-01 1.22985564e-01 6.22209728e-01 8.79304767e-01
 1.62932947e-01 5.91032386e-01 9.13548052e-01 1.88111737e-01
 5.72996378e-01 9.39373076e-01 2.05184534e-01 6.91838026e-01
 8.76748681e-01 9.28271264e-02 6.08935356e-01 9.11519170e-01
 1.39487609e-01 5.76817513e-01 9.46327329e-01 1.65457815e-01
 5.60834169e-01 9.75587428e-01 1.82171836e-01 6.94581270e-01
 9.14899647e-01 6.56557083e-02 6.08768761e-01 9.42318141e-01
 1.03939645e-01 5.78175604e-01 9.73119020e-01 1.28170028e-01
 5.67104578e-01 1.00020838e+00 1.43481493e-01 7.08221495e-01
 9.56053674e-01 4.19174433e-02 6.31618559e-01 9.82140839e-01
 6.85344115e-02 5.98932266e-01 1.00606000e+00 8.76441002e-02
 5.83983302e-01 1.02873385e+00 1.01731509e-01]
Keypoints: [ 9.73784566e-01

Keypoints: [ 2.97746837e-01  5.75515509e-01 -3.74869069e-09  3.48530442e-01
  6.97064996e-01 -8.01079944e-02  3.22871238e-01  8.31536829e-01
 -1.34118721e-01  2.66542733e-01  9.07978296e-01 -1.86854854e-01
  2.22717792e-01  9.56697524e-01 -2.43598714e-01  1.19190373e-01
  8.44603896e-01 -1.22303948e-01  4.78025563e-02  9.11901772e-01
 -1.90135539e-01  8.66664797e-02  8.97593737e-01 -2.32873961e-01
  1.37804955e-01  8.82931352e-01 -2.62427419e-01  4.84143682e-02
  7.70624518e-01 -1.25181630e-01  6.93891346e-02  7.86083817e-01
 -2.29446769e-01  1.92764282e-01  7.05753267e-01 -2.80081242e-01
  3.00876290e-01  6.41453147e-01 -3.00982952e-01  1.09854341e-02
  6.95382237e-01 -1.28788054e-01  5.68707064e-02  6.91744506e-01
 -2.18437925e-01  1.76717505e-01  6.30151868e-01 -2.47289792e-01
  2.80737340e-01  5.83084404e-01 -2.56227702e-01 -5.39234281e-03
  6.17802203e-01 -1.42727479e-01  3.44372839e-02  6.18149996e-01
 -2.00114727e-01  1.26047522e-01  5.88245809e-01 -2.20787004e-01
  2.05582067e-